### Asr evaluation

- Будем тестировать несколько аср моделей на общих сетах + на сете с голосовыми командами на русском языке для редактирования
- Тестить собираемся:
    - Whisper
    - GigaAM-v3
    - T-one
    - Vosk
    - VNIDIA Paraleet-TDT-0.6B-v3
    - wav2vec2-large-xlsr-53-russian

In [1]:
# # base
# !pip install torch torchaudio soundfile datasets huggingface_hub

# # t-one
# !pip install numpy "huggingface-hub>=0.14.0,<1.0.0" "onnxruntime>=1.12.0,<1.20.0" "pyctcdecode>=0.2.0,<1.0.0" "kenlm>=0.2.0,<1.0.0" miniaudio

# # Parakeet
# !pip install nemo-toolkit[asr]

# # wav2vec2
# !pip install "transformers[torch]" accelerate peft timm

# # VOSK
# !pip install vosk

In [1]:
import librosa
import torch
from transformers import WhisperProcessor, WhisperForConditionalGeneration, AutoModel
import torchaudio
from pathlib import Path
import soundfile as sf
import sys
from IPython.display import Audio
import wave
import json
import tempfile

In [2]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
device

device(type='cuda')

In [3]:
def load_audio_torchaudio(path: Path, target_sr: int = 16000):
    waveform, sr = torchaudio.load(str(path))
    if sr != target_sr:
        waveform = torchaudio.functional.resample(waveform, sr, target_sr)
        sr = target_sr
    if waveform.shape[0] > 1:
        waveform = waveform.mean(dim=0, keepdim=True)
    return waveform, sr

def load_audio_numpy(path: Path, target_sr: int = 16000):
    audio_np, sr = sf.read(str(path), dtype="float32")
    if sr != target_sr:
        import warnings
        warnings.warn(f"Expected {target_sr} Hz, got {sr}. Resample audio beforehand.")
    return audio_np, sr

In [4]:
SAMPLE_ONE = Path("/home/sallundina/tts/data/chern/1479acdc067b9e61802c318f0539995b.wav")
SAMPLE_TWO = Path('/home/sallundina/tts/initial_audio/audio_speaker-S_07_seg-005_45315837-45700918.wav')
SAMPLE_THREE = Path('/home/sallundina/tts/initial_audio/132.zhizn-v-chuzhoj-strane_speaker-S_02_seg-004_16518889-18437945.wav')

In [5]:
Audio(SAMPLE_ONE)

In [6]:
Audio(SAMPLE_TWO)

In [7]:
Audio(SAMPLE_THREE)

### Whisper

In [8]:
whisper_model_name = "openai/whisper-small"
whisper_processor = WhisperProcessor.from_pretrained(whisper_model_name)
whisper_model = WhisperForConditionalGeneration.from_pretrained(whisper_model_name).to(device)

In [9]:
def transcribe_whisper(audio_input, sr=None, language='ru'):
    WHISPER_SR = 16000
    
    if isinstance(audio_input, str):
        audio_array = librosa.load(audio_input, sr=WHISPER_SR, mono=True)[0]
        sr = WHISPER_SR
    else:
        audio_array = audio_input
        if sr is None:
            sr = WHISPER_SR
        elif sr != WHISPER_SR:
            audio_array = librosa.resample(audio_array, orig_sr=sr, target_sr=WHISPER_SR)
            sr = WHISPER_SR
    
    input_features = whisper_processor(audio_array, sampling_rate=sr, return_tensors="pt").input_features.to(device)
    
    generated_ids = whisper_model.generate(
        input_features,
        language=language,
        task="transcribe"
    )
    
    transcription = whisper_processor.batch_decode(generated_ids, skip_special_tokens=True)[0]
    return transcription.lower()

In [10]:
transcribe_whisper('/data/sallundina/operators_09_25/operators_09_25/Jukov/000000_015075_Jukov.wav')

The attention mask is not set and cannot be inferred from input because pad token is same as eos token. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.


' я понял.'

In [11]:
transcribe_whisper('/data/sallundina/tts_datasets_rus/Pik_speaker/original_audio/fee5af9e141f5db38ef48e4898c78c66.flac')

' время ожидания составит 10 минут.'

In [12]:
transcribe_whisper(str(SAMPLE_ONE))

' и вот потом мы познакомились с этой девочкой, которая поёт. вообще, исландия очень славится своими голосами, своими музыкантами. они очень такие самобытные и очень модные. бьёрк же оттуда вышла.'

In [13]:
transcribe_whisper(str(SAMPLE_TWO))

' а некоторые вот блин делали похожи на энтузиазм из-за своей деньги вообще в свое время. и все это озвучено, есть даже какие-то cgi заставки.'

In [14]:
# оборванный текст
transcribe_whisper(str(SAMPLE_THREE))

' решение и ваше желание понять. нет ничего хорошего или плохого. все является таким, таким мы его видим. и если вдруг вы замечаете, что в том месте, куда вы переехали, ну предположим вы переехали в западную европу, да, из россии, потому что я знаю, что у каждого из вас своя история, ну предположим вы переехали в западную европу и вы ощущаете, что к русскими здесь плохо относится. скажу сразу, что по большей части это внутреннее отношение к'

### GigaAM-v3

In [15]:
revision = "e2e_rnnt"
model = AutoModel.from_pretrained(
    "ai-sage/GigaAM-v3",
    revision=revision,
    trust_remote_code=True,
)

In [16]:
transcription = model.transcribe('/data/sallundina/operators_09_25/operators_09_25/Jukov/000000_015075_Jukov.wav')
print(transcription)

Я понял.


In [17]:
transcription = model.transcribe('/data/sallundina/tts_datasets_rus/Pik_speaker/original_audio/fee5af9e141f5db38ef48e4898c78c66.flac')
print(transcription)

Время ожидания составит 10 минут.


In [18]:
transcription = model.transcribe(str(SAMPLE_ONE))
print(transcription)

И-и-и вот потом мы познакомились с этой девочкой, которая поёт. Вообще Исландия очень славится своими голосами, своими музыкантами. Они очень такие самобытные и очень модные. Бьорг же оттуда вышла.


In [19]:
transcription = model.transcribe(str(SAMPLE_TWO))
print(transcription)

А некоторые вот, блин, делали похоже на энтузиазм не за свои деньги вообще в своё время. И всё это озвучено, и есть даже какие-то CJ-заставки.


### T-one

In [20]:
tone_repo_path = Path("/tmp/T-one")
if not tone_repo_path.exists():
    import subprocess
    subprocess.run(["git", "clone", "https://github.com/voicekit-team/T-one.git", str(tone_repo_path)], check=True)

sys.path.insert(0, str(tone_repo_path))

In [21]:
from tone import StreamingCTCPipeline, read_audio

pipeline = StreamingCTCPipeline.from_hugging_face()

In [22]:
audio = read_audio(str(SAMPLE_ONE))
phrases = pipeline.forward_offline(audio)

for p in phrases:
    print(f"[{p.start_time:.2f}–{p.end_time:.2f}] {p.text}")

[0.63–3.00] и вот потом мы познакомились с этой девочкой
[3.78–4.62] которая поет
[5.31–13.41] вообще исландия очень славится своими голосами своими музыкантами они очень такие самобытные и очень модные бьорк же оттуда вышла


In [23]:
audio = read_audio(str(SAMPLE_TWO))
phrases = pipeline.forward_offline(audio)

for p in phrases:
    print(f"[{p.start_time:.2f}–{p.end_time:.2f}] {p.text}")

[0.30–4.14] а некоторые вот блин делали похоже на энтузиазм и за свои деньги вообще в свое время
[5.13–8.40] и все это озвучено и есть даже какие то сидай заставки


In [24]:
audio = read_audio(str(SAMPLE_THREE))
phrases = pipeline.forward_offline(audio)

# непохоже получилось
for p in phrases:
    print(f"[{p.start_time:.2f}–{p.end_time:.2f}] {p.text}")

[0.39–3.51] решение и ваше желание понять нет ничего
[4.23–8.25] хорошего или плохого все является таким каким мы его
[8.85–11.19] видим и если вдруг вы замечаете что
[12.03–34.05] в том месте куда вы переехали но предположим мы переехали в западную европу из россии потому что я знаю что у каждого из вас своя история но предположим мы приехали в западную европу и вы ощущаете что к русским не весь плохо относится скажу сразу что по большей части это внутреннее отношение человека к семье и к своей родине к тому месту откуда он приехал
[34.74–35.88] мир как и зеркало
[36.63–37.77] он отравит то
[38.46–40.11] что усами о себе думаете
[40.95–43.35] и всегда оправдает ваши ожидания


### NVIDIA Parakeet-TDT-0.6B-v3

In [25]:
import nemo.collections.asr as nemo_asr

asr_model = nemo_asr.models.ASRModel.from_pretrained(model_name="nvidia/parakeet-tdt-0.6b-v3")

asr_model.eval()

if hasattr(asr_model, 'decoding'):
    if hasattr(asr_model.decoding, 'decoding_computer'):
        decoding_computer = asr_model.decoding.decoding_computer
        if hasattr(decoding_computer, 'cuda_graphs_mode'):
            decoding_computer.cuda_graphs_mode = None
        if hasattr(asr_model.decoding, 'cfg') and hasattr(asr_model.decoding.cfg, 'cuda_graphs_mode'):
            asr_model.decoding.cfg.cuda_graphs_mode = None

[NeMo W 2025-12-07 04:53:22 nemo_logging:405] Megatron num_microbatches_calculator not found, using Apex version.
OneLogger: Setting error_handling_strategy to DISABLE_QUIETLY_AND_REPORT_METRIC_ERROR for rank (rank=0) with OneLogger disabled. To override: explicitly set error_handling_strategy parameter.
No exporters were provided. This means that no telemetry data will be collected.


[NeMo I 2025-12-07 04:53:30 nemo_logging:393] Tokenizer SentencePieceTokenizer initialized with 8192 tokens


[NeMo W 2025-12-07 04:53:34 nemo_logging:405] If you intend to do training or fine-tuning, please call the ModelPT.setup_training_data() method and provide a valid configuration file to setup the train data loader.
    Train config : 
    use_lhotse: true
    skip_missing_manifest_entries: true
    input_cfg: null
    tarred_audio_filepaths: null
    manifest_filepath: null
    sample_rate: 16000
    shuffle: true
    num_workers: 2
    pin_memory: true
    max_duration: 10.0
    min_duration: 1.0
    text_field: answer
    batch_duration: null
    max_tps: null
    use_bucketing: true
    bucket_duration_bins: null
    bucket_batch_size: null
    num_buckets: 30
    bucket_buffer_size: 20000
    shuffle_buffer_size: 10000
    
[NeMo W 2025-12-07 04:53:34 nemo_logging:405] If you intend to do validation, please call the ModelPT.setup_validation_data() or ModelPT.setup_multiple_validation_data() method and provide a valid configuration file to setup the validation data loader(s). 
    V

[NeMo I 2025-12-07 04:53:34 nemo_logging:393] PADDING: 0
[NeMo I 2025-12-07 04:53:40 nemo_logging:393] Using RNNT Loss : tdt
    Loss tdt_kwargs: {'fastemit_lambda': 0.0, 'clamp': -1.0, 'durations': [0, 1, 2, 3, 4], 'sigma': 0.02, 'omega': 0.1}
[NeMo I 2025-12-07 04:53:40 nemo_logging:393] Using RNNT Loss : tdt
    Loss tdt_kwargs: {'fastemit_lambda': 0.0, 'clamp': -1.0, 'durations': [0, 1, 2, 3, 4], 'sigma': 0.02, 'omega': 0.1}
[NeMo I 2025-12-07 04:53:40 nemo_logging:393] Using RNNT Loss : tdt
    Loss tdt_kwargs: {'fastemit_lambda': 0.0, 'clamp': -1.0, 'durations': [0, 1, 2, 3, 4], 'sigma': 0.02, 'omega': 0.1}
[NeMo I 2025-12-07 04:53:43 nemo_logging:393] Model EncDecRNNTBPEModel was successfully restored from /home/sallundina/.cache/huggingface/hub/models--nvidia--parakeet-tdt-0.6b-v3/snapshots/6d590f77001d318fb17a0b5bf7ee329a91b52598/parakeet-tdt-0.6b-v3.nemo.


In [26]:
asr_model_cpu = asr_model.cpu()
if hasattr(asr_model_cpu, 'decoding') and hasattr(asr_model_cpu.decoding, 'decoding_computer'):
    if hasattr(asr_model_cpu.decoding.decoding_computer, 'cuda_graphs_mode'):
        asr_model_cpu.decoding.decoding_computer.cuda_graphs_mode = None
        
outputs = asr_model.transcribe([str(SAMPLE_ONE)], batch_size=1, num_workers=0)

for out in outputs:
    text = getattr(out, "text", out)
    print(text)

[NeMo W 2025-12-07 04:53:44 nemo_logging:405] The following configuration keys are ignored by Lhotse dataloader: use_start_end_token
[NeMo W 2025-12-07 04:53:44 nemo_logging:405] You are using a non-tarred dataset and requested tokenization during data sampling (pretokenize=True). This will cause the tokenization to happen in the main (GPU) process,possibly impacting the training speed if your tokenizer is very large.If the impact is noticable, set pretokenize=False in dataloader config.(note: that will disable token-per-second filtering and 2D bucketing features)
Transcribing: 1it [00:01,  1.01s/it]

И вот потом мы познакомились с этой девочкой, которая поет. Вообще Исландия очень славится своими голосами, своими музыкантами. Они очень такие самобытные и очень модные. Бьорг же оттуда вышла.


In [27]:
asr_model_cpu = asr_model.cpu()
if hasattr(asr_model_cpu, 'decoding') and hasattr(asr_model_cpu.decoding, 'decoding_computer'):
    if hasattr(asr_model_cpu.decoding.decoding_computer, 'cuda_graphs_mode'):
        asr_model_cpu.decoding.decoding_computer.cuda_graphs_mode = None

outputs = asr_model_cpu.transcribe([str(SAMPLE_TWO)], timestamps=True, batch_size=1, num_workers=0)

res = outputs[0]
text = getattr(res, "text", res)
print("TEXT:", text)

if hasattr(res, "timestamp") and isinstance(res.timestamp, dict):
    print("\nWORD TIMESTAMPS:")
    for stamp in res.timestamp.get("word", []):
        print(f"[{stamp['start']:.2f}–{stamp['end']:.2f}] {stamp['word']}")

[NeMo I 2025-12-07 04:53:45 nemo_logging:393] Timestamps requested, setting decoding timestamps to True. Capture them in Hypothesis object,                         with output[0][idx].timestep['word'/'segment'/'char']
[NeMo I 2025-12-07 04:53:45 nemo_logging:393] Using RNNT Loss : tdt
    Loss tdt_kwargs: {'fastemit_lambda': 0.0, 'clamp': -1.0, 'durations': [0, 1, 2, 3, 4], 'sigma': 0.02, 'omega': 0.1}


[NeMo W 2025-12-07 04:53:45 nemo_logging:405] The following configuration keys are ignored by Lhotse dataloader: use_start_end_token
[NeMo W 2025-12-07 04:53:45 nemo_logging:405] You are using a non-tarred dataset and requested tokenization during data sampling (pretokenize=True). This will cause the tokenization to happen in the main (GPU) process,possibly impacting the training speed if your tokenizer is very large.If the impact is noticable, set pretokenize=False in dataloader config.(note: that will disable token-per-second filtering and 2D bucketing features)
Transcribing: 1it [00:01,  1.42s/it]

TEXT: А некоторые, вот, блин, делали похожие на энтузиазм и за свои деньги вообще в свое время. И все это озвучено, есть даже какие-то CJ заставки.

WORD TIMESTAMPS:
[0.00–0.16] А
[0.16–0.56] некоторые,
[0.64–0.80] вот,
[0.88–1.04] блин,
[1.20–1.52] делали
[1.60–2.00] похожие
[2.00–2.08] на
[2.08–2.64] энтузиазм
[2.72–2.80] и
[2.80–2.88] за
[2.88–3.12] свои
[3.12–3.36] деньги
[3.44–3.68] вообще
[3.68–3.76] в
[3.76–4.08] свое
[4.08–4.40] время.
[4.80–5.04] И
[5.04–5.28] все
[5.28–5.52] это
[5.52–6.16] озвучено,
[6.24–6.56] есть
[6.56–6.88] даже
[6.88–7.44] какие-то
[7.44–7.68] CJ
[8.00–8.56] заставки.


In [28]:
asr_model_cpu = asr_model.cpu()
if hasattr(asr_model_cpu, 'decoding') and hasattr(asr_model_cpu.decoding, 'decoding_computer'):
    if hasattr(asr_model_cpu.decoding.decoding_computer, 'cuda_graphs_mode'):
        asr_model_cpu.decoding.decoding_computer.cuda_graphs_mode = None
        
outputs = asr_model.transcribe([str(SAMPLE_THREE)], batch_size=1, num_workers=0)

for out in outputs:
    text = getattr(out, "text", out)
    print(text)

[NeMo W 2025-12-07 04:53:47 nemo_logging:405] The following configuration keys are ignored by Lhotse dataloader: use_start_end_token
[NeMo W 2025-12-07 04:53:47 nemo_logging:405] You are using a non-tarred dataset and requested tokenization during data sampling (pretokenize=True). This will cause the tokenization to happen in the main (GPU) process,possibly impacting the training speed if your tokenizer is very large.If the impact is noticable, set pretokenize=False in dataloader config.(note: that will disable token-per-second filtering and 2D bucketing features)
Transcribing: 1it [00:01,  1.64s/it]

Решение и ваше желание понять нет ничего хорошего или плохого. Все является таким, каким мы его видим. И если вдруг вы замечаете, что в том месте, куда вы переехали, ну, предположим, вы переехали в Западную Европу, да, из России. Потому что я знаю, что у каждого из вас своя история. Но, предположим, вы переехали в Западную Европу, и вы ощущаете, что к русским здесь плохо относятся. Скажу сразу, что по большей части это внутреннее отношение человека к себе и к своей родине, к тому месту, откуда он приехал. Мир, как зеркало- он отразит то, что вы сами о себе думаете, и всегда оправдает ваши ожидания.


### wav2vec2-large-xlsr-53-russian

In [29]:
from transformers import Wav2Vec2Processor, Wav2Vec2ForCTC

w2v_model_name = "jonatasgrosman/wav2vec2-large-xlsr-53-russian"

w2v_processor = Wav2Vec2Processor.from_pretrained(w2v_model_name)
w2v_model = Wav2Vec2ForCTC.from_pretrained(w2v_model_name).to(device)

In [30]:
waveform, sr = load_audio_torchaudio(SAMPLE_ONE, target_sr=16_000)
input_values = w2v_processor(waveform.squeeze(0), sampling_rate=16_000, return_tensors="pt").input_values.to(device)

with torch.no_grad():
    logits = w2v_model(input_values).logits

pred_ids = torch.argmax(logits, dim=-1)
transcription_w2v = w2v_processor.batch_decode(pred_ids)[0]
print(transcription_w2v)

и вот потом и познакомились с этой девочкой которая поют в обще исланде очень слабится своими голосами своими музыкантами они очень такие самобытные и очень модные бьоргже оттуда вышла


In [31]:
waveform, sr = load_audio_torchaudio(SAMPLE_TWO, target_sr=16_000)
input_values = w2v_processor(waveform.squeeze(0), sampling_rate=16_000, return_tensors="pt").input_values.to(device)

with torch.no_grad():
    logits = w2v_model(input_values).logits

pred_ids = torch.argmax(logits, dim=-1)
transcription_w2v = w2v_processor.batch_decode(pred_ids)[0]
print(transcription_w2v)

а некоторые вот блинг делали похоже на энтузиазме и за свои деньги вообще свое время и все это озвученно есть даже какие-то сиджай заставки


In [32]:
waveform, sr = load_audio_torchaudio(SAMPLE_THREE, target_sr=16_000)
input_values = w2v_processor(waveform.squeeze(0), sampling_rate=16_000, return_tensors="pt").input_values.to(device)

with torch.no_grad():
    logits = w2v_model(input_values).logits

pred_ids = torch.argmax(logits, dim=-1)
transcription_w2v = w2v_processor.batch_decode(pred_ids)[0]
print(transcription_w2v)

решение и ваше желание понять нет ничего хорошего или плохого всё является таким таким мы его видим  если вдругого замечается что в том месте куда вы переехали но предполжим и приехали западную егро куда из россии потом что езнае что каждого из вас своя история мы предположм ми приехали в западную европу и вы ощущается что крузким здесь плохо относятся  скажу сразу что по большей части это внутреннее отношене человека к себе и к своей родиник тому месту о кутоон приехал  мир как зеркало он отразит то что сами о себе думается и всегда оправдает ваши ожидания


### VOSK

In [33]:
# !wget https://alphacephei.com/vosk/models/vosk-model-small-ru-0.22.zip
# !unzip vosk-model-small-ru-0.22.zip -d models/
# !mv models/vosk-model-small-ru-0.22 models/vosk-model-small-ru

In [34]:
from vosk import Model, KaldiRecognizer

VOSK_MODEL_PATH = "models/vosk-model-small-ru"

model_files = list(Path(VOSK_MODEL_PATH).glob("*"))
vosk_model = Model(VOSK_MODEL_PATH)

LOG (VoskAPI:ReadDataFiles():model.cc:213) Decoding params beam=10 max-active=3000 lattice-beam=2
LOG (VoskAPI:ReadDataFiles():model.cc:216) Silence phones 1:2:3:4:5:6:7:8:9:10
LOG (VoskAPI:RemoveOrphanNodes():nnet-nnet.cc:948) Removed 0 orphan nodes.
LOG (VoskAPI:RemoveOrphanComponents():nnet-nnet.cc:847) Removing 0 orphan components.
LOG (VoskAPI:ReadDataFiles():model.cc:248) Loading i-vector extractor from models/vosk-model-small-ru/ivector/final.ie
LOG (VoskAPI:ComputeDerivedVars():ivector-extractor.cc:183) Computing derived variables for iVector extractor
LOG (VoskAPI:ComputeDerivedVars():ivector-extractor.cc:204) Done.
LOG (VoskAPI:ReadDataFiles():model.cc:282) Loading HCL and G from models/vosk-model-small-ru/graph/HCLr.fst models/vosk-model-small-ru/graph/Gr.fst
LOG (VoskAPI:ReadDataFiles():model.cc:308) Loading winfo models/vosk-model-small-ru/graph/phones/word_boundary.int


In [36]:
def prepare_audio_for_vosk(audio_path):
    wf = wave.open(str(audio_path), "rb")
    channels = wf.getnchannels()
    sample_width = wf.getsampwidth()
    sample_rate = wf.getframerate()
    wf.close()
    
    needs_conversion = (channels != 1 or sample_width != 2 or sample_rate != 16000)
    temp_wav_path = None
    
    if needs_conversion:
        audio_data, sr = sf.read(str(audio_path), dtype='float32')
        
        if len(audio_data.shape) > 1 and audio_data.shape[1] > 1:
            audio_data = audio_data.mean(axis=1)
        
        if sr != 16000:
            audio_tensor = torch.from_numpy(audio_data).unsqueeze(0)
            audio_tensor = torchaudio.functional.resample(audio_tensor, sr, 16000)
            audio_data = audio_tensor.squeeze(0).numpy()
            sr = 16000
        
        temp_wav = tempfile.NamedTemporaryFile(suffix='.wav', delete=False)
        temp_wav_path = temp_wav.name
        temp_wav.close()
        
        sf.write(temp_wav_path, audio_data, 16000, subtype='PCM_16', format='WAV')
        
        wf = wave.open(temp_wav_path, "rb")
    else:
        wf = wave.open(str(audio_path), "rb")
    
    return wf, temp_wav_path, needs_conversion

In [37]:
wf, temp_wav_path, needs_conversion = prepare_audio_for_vosk(SAMPLE_ONE)

rec = KaldiRecognizer(vosk_model, wf.getframerate())

results = []
while True:
    data = wf.readframes(4000)
    if len(data) == 0:
        break
    if rec.AcceptWaveform(data):
        part = json.loads(rec.Result())
        results.append(part)

final = json.loads(rec.FinalResult())
results.append(final)

wf.close()

if needs_conversion:
    import os
    os.unlink(temp_wav_path)

full_text = " ".join(r.get("text", "") for r in results).strip()
print(full_text)

и вот потом и познакомились этой девочкой которая поёт вообще исландии очень славится своими голосами своими музыкантами они очень такие самобытные и очень модные бёрк же оттуда вышло


In [38]:
wf, temp_wav_path, needs_conversion = prepare_audio_for_vosk(SAMPLE_TWO)

rec = KaldiRecognizer(vosk_model, wf.getframerate())

results = []
while True:
    data = wf.readframes(4000)
    if len(data) == 0:
        break
    if rec.AcceptWaveform(data):
        part = json.loads(rec.Result())
        results.append(part)

final = json.loads(rec.FinalResult())
results.append(final)

wf.close()

if needs_conversion:
    import os
    os.unlink(temp_wav_path)

full_text = " ".join(r.get("text", "") for r in results).strip()
print(full_text)

а некоторые вот блин делали похож на энтузиазме за свои деньги вообще своё время и все это озвученные есть даже какие то си джей заставки


In [39]:
wf, temp_wav_path, needs_conversion = prepare_audio_for_vosk(SAMPLE_THREE)

rec = KaldiRecognizer(vosk_model, wf.getframerate())

results = []
while True:
    data = wf.readframes(4000)
    if len(data) == 0:
        break
    if rec.AcceptWaveform(data):
        part = json.loads(rec.Result())
        results.append(part)

final = json.loads(rec.FinalResult())
results.append(final)

wf.close()

if needs_conversion:
    import os
    os.unlink(temp_wav_path)

full_text = " ".join(r.get("text", "") for r in results).strip()
print(full_text)

решение и ваше желание понять не ничего хорошего или плохого все является таким каким мы его видим если вдруг вы замечаете что в том месте куда вы переехали но предположим переехали западную европу да из россии потому что я знаю что у каждого из вас своя история на предположим приехали в западную европу и вы ощущается штук русскими здесь плохо относится скажу сразу что по большей части это внутренние отношение человека к себе и к своей родине к тому месту откуда он приехал мир как и зеркало он отразит то что сами о себе думаете и всегда оправдает ваши ожидания


Vosk, wav2vec2 и t-one даже в первом приближении плохо справились, поэтому дальше их тестировать не будем (кроме T-one, дадим ему шанс).